# Сравнение наивного и оптимизированного алгоритмов вычисления циклической свертки с преобразованием Фурье от размера ранга округления

In [1]:
%load_ext autoreload

In [2]:
%autoreload 2

import time
from collections import defaultdict
import matplotlib.pyplot as plt
import seaborn as sns
import itertools
import numpy as np
import pandas as pd

from bilinear_package.src import hadamard_product, random_tensor_generation, rounding, primitives, convolution

from experiments_stuff import get_tensor_for_experiment, default_dict_to_df

In [5]:
from experiments_stuff import get_random_tensor_for_experiment


answer = defaultdict(lambda : [])
answer2 = defaultdict(lambda : [])
answer3 = defaultdict(lambda : [])
grid_modes = np.arange(5, 101, 5)
tries = 5

for i in grid_modes:
    tt_tensors1 = []
    tt_tensors2 = []
    tt_tensors_random = []
    for j in range(tries):
        n = 6
        d = 15
        r = 10
        tt_tensors1.append(get_tensor_for_experiment(n, d, r, 1, 3 * j + 1))
        tt_tensors2.append(get_tensor_for_experiment(n, d, r, 1, 3 * j + 2))
        tt_tensors_random.append(get_random_tensor_for_experiment(n, d, i, 3 * j + 3))
    
    for j in range(tries):
        time1 = time.time()
        hadamard_product.generalizedApproximateHadamardProduct(tt_tensors1 = convolution.countFourier(tt_tensors1[j]), tt_tensors2 = convolution.countFourier(tt_tensors2[j]), random_tensor = convolution.countInverseFourier(tt_tensors_random[j]), func = lambda z: np.fft.ifft(z, axis=2))
        time2 = time.time()
        precise_cycle_convolution = convolution.preciseCycleConvolution(tt_tensors1[j], tt_tensors2[j])
        rounded_tensor = rounding.randomizeThenOrthogonalize(precise_cycle_convolution, tt_tensors_random[j])
        time3 = time.time()
        answer[i].append(time2 - time1)
        answer2[i].append(time3 - time2)
        answer3[i].append(primitives.ttTensorsUnsymmetricalRelativeComparance(rounded_tensor, precise_cycle_convolution))



# print(dict(answer))
# print(dict(answer2))
# print(dict(answer3))

[array([[-1.14263061e-01-1.18798480e-18j,  1.64265580e-01-1.43800124e-17j,
         3.66113674e-03+3.21699528e-18j,  1.09537400e-01+1.99205219e-17j,
         6.41798443e-03+7.23243110e-18j],
       [ 1.10091303e-02-5.66095226e-18j, -6.18864456e-02-2.61938146e-18j,
        -7.39339666e-02+2.56654006e-17j,  4.12767081e-01-3.22804161e-17j,
         1.26676934e-01-7.71396494e-18j],
       [ 3.34585269e-02-6.92484205e-18j,  1.29420004e-01-2.51165589e-18j,
        -2.49874725e-02+2.69440659e-18j,  1.86183944e-01-1.08874142e-17j,
        -1.72893612e-02+4.61541352e-18j],
       [ 1.83852332e-01-2.68281196e-17j, -7.24712256e-02-7.11037670e-18j,
         1.29628188e-02+1.54938598e-17j,  3.90791032e-02-2.81480156e-17j,
         1.49063073e-01+6.58264147e-18j],
       [-2.58496761e-02+6.54497384e-18j, -4.71732036e-02-9.47277793e-18j,
        -7.41500110e-02+5.42049631e-18j,  9.26690792e-02-2.36851476e-17j,
        -1.06964301e-01-1.45359984e-18j],
       [ 1.58310137e-01+1.45459946e-18j,  8.60129

KeyboardInterrupt: 

In [ ]:
default_dict_to_df(answer, save_path="experiments_results/exp5_approximate_time.csv")
default_dict_to_df(answer2, save_path="experiments_results/exp5_precise_rounding_time.csv")
default_dict_to_df(answer3, save_path="experiments_results/exp5_precision_time.csv")